# Traitement des données de financements 

In [ ]:
#importer les packages
import pandas as pd
import numpy as np
from code_utils.utils import extract_first_name,replace_all,get_scanR_structure
from code_utils.cached_data_handler import get_structure, get_person
from code_utils.features_into_dictionnary import persons, projects, address
from tqdm import tqdm
import pprint as pp
tqdm.pandas()
from code_utils.pickle import load_cache,write_cache
import os
from dotenv import load_dotenv

load_dotenv()

Authorization = os.getenv('Authorization_access_185')
Authorization_ORCID = os.getenv('Authorization_cluster_BSO_ORCID')
url_cluster = os.getenv('url_cluster')

In [2]:
sources=pd.read_json('sources.json')

In [3]:
source=list(sources.keys())[0]
source

'ANR'

In [5]:
#cache structures, personnes et orcid avec differentes sources de donnees
cached_data = {}
try:
    cached_data = load_cache(cached_data,f"./DATA/{source}/caches/cached_{source.lower()}_data.pkl")
except:
    write_cache(cached_data,f"./DATA/{source}/caches/cached_{source.lower()}_data.pkl")
    
cached_data_persons = {}
try:
    cached_data_persons = load_cache(cached_data_persons,f"./DATA/{source}/caches/cached_{source.lower()}_data_persons.pkl")
except:
    write_cache(cached_data_persons,f"./DATA/{source}/caches/cached_{source.lower()}_data_persons.pkl")
    
cached_data_orcid = {}
try:
    cached_data_orcid = load_cache(cached_data_orcid,f"./DATA/{source}/caches/cached_{source.lower()}_data_orcid.pkl")
except:
    write_cache(cached_data_orcid,f"./DATA/{source}/caches/cached_{source.lower()}_data_orcid.pkl")

# Données partenaires

In [6]:
# amener les partenaires depuis le site 
if source=='ANR':
    page_partenaires_10 = requests.get(sources[source]['url_partenaires']).json()
    colonnes_partenaires_10 = page_partenaires_10['columns']
    donnees_partenaires_10 = page_partenaires_10['data']
    df_partenaires=pd.DataFrame(data=donnees_partenaires_10,columns=colonnes_partenaires_10)
elif source=='ANSES':
    df_from_anses=pd.read_excel(sources[source]['url_partenaires'])
    df=df_from_anses.iloc[1:,:]
    df.columns=list(df_from_anses.iloc[0,:])
    dict_equipe={list(df_from_anses.columns)[k].replace('Équipe 10 ','Équipe 10').replace('Équipe13','Équipe 13'):k for k in range (len(list(df_from_anses.columns))) if list(df_from_anses.columns)[k].find('Équipe')>=0}
    list_df=[]
    number=3
    for n in range(1,len(dict_equipe)+1):
        equipe_n=pd.concat([df.iloc[:,0:3],df.iloc[:,number:number+6]], axis=1)
        list_df.append(equipe_n)
        number+=6
    df_partenaires=pd.concat([list_df[k].dropna(subset=[sources[source]['nom'], sources[source]['prenom'],sources[source]['nom_structure'], sources[source]['nom'], 'Pays'], how='all') for k in range(len(list_df))])
    
elif source=='IRESP':
    df_partenaires1=pd.read_csv(sources[source]['url_partenaires1'] ,sep=";", encoding='UTF-8')
    df_partenaires2=pd.read_csv(sources[source]['url_partenaires2'] ,sep=";", encoding='UTF-8')
    df_partenaires=pd.concat([df_partenaires1,df_partenaires2])
elif source=='ADEME':
    df_partenaires=pd.read_csv(sources[source]['url_partenaires'] ,sep=",", encoding='ISO-8859-1', on_bad_lines='skip')
else:    
    df_partenaires=pd.read_csv(sources[source]['url_partenaires'] ,sep=";", encoding='ISO-8859-1')

df_partenaires=df_partenaires.reset_index()
del df_partenaires['index']

# Matcher établissement

In [7]:
id_struct=df_partenaires
id_struct[f"{sources[source]['nom_structure']}2"]=id_struct.loc[:,sources[source]['nom_structure']].apply(lambda x: replace_all(str(x).lower().replace(" d e"," d'e").replace(" d a"," d'a").replace(" d i"," d'i").replace(" d o"," d'o").replace(" d u"," d'u").replace(" d y"," d'y").replace(" d h"," d'h").replace(" l e"," l'e").replace(" l a"," l'a").replace(" l i"," l'i").replace(" l o"," l'o").replace(" l u"," l'u").replace(" l y"," l'y").replace(" l h"," l'h")))
id_struct=id_struct.drop_duplicates(subset=[f"{sources[source]['nom_structure']}2"])

In [ ]:
id_struct.progress_apply(lambda row: get_structure(row,source,cached_data,sources[source]['nom_structure'],sources[source]['ville'],sources[source]['pays'],sources[source]['code_projet'],False), axis=1) 
write_cache(cached_data,f"./DATA/{source}/caches/cached_{source}_data.pkl")

100%|██████████| 26586/26586 [10:01:02<00:00,  1.36s/it]  


In [9]:
len(cached_data)

26586

In [10]:
id_struct['id_structure_matcher']=id_struct.loc[:,sources[source]['nom_structure']].apply(lambda x: cached_data[x])

C:\Users\haallat\AppData\Local\Temp\ipykernel_4372\3780844401.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  id_struct['id_structure_matcher']=id_struct.loc[:,sources[source]['nom_structure']].apply(lambda x: cached_data[x])


In [11]:
id_struct

Projet.Code_Decision_ANR Projet.Acronyme  \
0             ANR-24-SRSE-0016         MINerVA   
1             ANR-24-SRSE-0015            ADDI   
2             ANR-24-SRSE-0014       IMPACTING   
3             ANR-24-SRSE-0013         MERKATO   
4             ANR-24-SRSE-0012     inTOLERABLE   
...                        ...             ...   
72080         ANR-10-AALI-0002            HOST   
72082         ANR-10-AALI-0002            HOST   
72083         ANR-10-AALI-0002            HOST   
72085         ANR-10-AALI-0001        ENTRANCE   
72087         ANR-10-AALI-0001        ENTRANCE   

      Projet.Partenaire.Code_Decision_ANR  Projet.Partenaire.Est_coordinateur  \
0                     ANR-24-SRSE-0016-01                                True   
1                     ANR-24-SRSE-0015-01                                True   
2                     ANR-24-SRSE-0014-01                                True   
3                     ANR-24-SRSE-0013-01                                True   
4                     ANR-24-SRSE-0012-01                                True   
...                                   ...                                 ...   
72080                 ANR-10-AALI-0002-03                               False   
72082                 ANR-10-AALI-0002-01                                True   
72083                 ANR-10-AALI-0002-02                               False   
72085                 ANR-10-AALI-0001-02                               False   
72087                 ANR-10-AALI-0001-04                               False   

                         Projet.Partenaire.Nom_organisme  \
0      Centre interdisciplinaire de recherche en biol...   
1                           UNIVERSITE TOULOUSE CAPITOLE   
2      Interactions hotes-vecteurs-parasites-environn...   
3      CENTRE TECHNIQUE INDUSTRIEL DE LA PLASTURGIE E...   
4      Institut Pasteur - Unité de Virus et interfére...   
...                                                  ...   
72080                               DEPARTEMENT DU RHÔNE   
72082        OFFICE PUBLIC DE L HABITAT DU RHÔNE (OPAC )   
72083                                              ADAMA   
72085                                 AUTONOM'LAB (ALAB)   
72087                     SPLITTED DESKTOP SYSTEMS (SDS)   

      Projet.Partenaire.Categorie_organisme Projet.Partenaire.Code_RNSR  \
0                    Organisme de recherche                  201119724W   
1                                Université                  199511949P   
2                    Organisme de recherche                  201320629W   
3                              Divers privé                        None   
4                             Divers public                  201321615T   
...                                     ...                         ...   
72080                         Divers public                        None   
72082                         Divers public                        None   
72083    PME (petite et moyenne entreprise)                        None   
72085                            Université                        None   
72087    PME (petite et moyenne entreprise)                        None   

      Projet.Partenaire.Responsable_scientifique.Nom  \
0                                             BRUNET   
1                                             GRANDI   
2                                           BARREAUX   
3                                               ROCA   
4                                              SALEH   
...                                              ...   
72080                                           None   
72082                                        DELOCHE   
72083                                           None   
72085                                           None   
72087                                           None   

      Projet.Partenaire.Responsable_scientifique.Prenom  \
0                                              Isabelle   
1                  

In [12]:
id_struct=id_struct.reset_index()
del id_struct['index']
id_struct.to_excel(f"./DATA/{source}/df_partenaires.xlsx")
id_struct.to_json(f"./DATA/{source}/df_partenaires.json")

In [13]:
id_struct=pd.read_json(f"./DATA/{source}/df_partenaires.json")
id_struct=id_struct[[sources[source]['nom_structure'],'id_structure_matcher']]
id_struct[f"{sources[source]['nom_structure']}2"]=id_struct.loc[:,sources[source]['nom_structure']].apply(lambda x: replace_all(str(x).lower().replace(" d e"," d'e").replace(" d a"," d'a").replace(" d i"," d'i").replace(" d o"," d'o").replace(" d u"," d'u").replace(" d y"," d'y").replace(" d h"," d'h").replace(" l e"," l'e").replace(" l a"," l'a").replace(" l i"," l'i").replace(" l o"," l'o").replace(" l u"," l'u").replace(" l y"," l'y").replace(" l h"," l'h")))

df_partenaires[f"{sources[source]['nom_structure']}2"]=df_partenaires.loc[:,sources[source]['nom_structure']].apply(lambda x: replace_all(str(x).lower().replace(" d e"," d'e").replace(" d a"," d'a").replace(" d i"," d'i").replace(" d o"," d'o").replace(" d u"," d'u").replace(" d y"," d'y").replace(" d h"," d'h").replace(" l e"," l'e").replace(" l a"," l'a").replace(" l i"," l'i").replace(" l o"," l'o").replace(" l u"," l'u").replace(" l y"," l'y").replace(" l h"," l'h")))
df_partenaires_struct=pd.merge(df_partenaires,id_struct[[f"{sources[source]['nom_structure']}2",'id_structure_matcher']], on=f"{sources[source]['nom_structure']}2", how='left')
df_partenaires_struct

Projet.Code_Decision_ANR Projet.Acronyme  \
0             ANR-24-SRSE-0016         MINerVA   
1             ANR-24-SRSE-0015            ADDI   
2             ANR-24-SRSE-0014       IMPACTING   
3             ANR-24-SRSE-0013         MERKATO   
4             ANR-24-SRSE-0012     inTOLERABLE   
...                        ...             ...   
72084         ANR-10-AALI-0001        ENTRANCE   
72085         ANR-10-AALI-0001        ENTRANCE   
72086         ANR-10-AALI-0001        ENTRANCE   
72087         ANR-10-AALI-0001        ENTRANCE   
72088         ANR-10-AALI-0001        ENTRANCE   

      Projet.Partenaire.Code_Decision_ANR  Projet.Partenaire.Est_coordinateur  \
0                     ANR-24-SRSE-0016-01                                True   
1                     ANR-24-SRSE-0015-01                                True   
2                     ANR-24-SRSE-0014-01                                True   
3                     ANR-24-SRSE-0013-01                                True   
4                     ANR-24-SRSE-0012-01                                True   
...                                   ...                                 ...   
72084                 ANR-10-AALI-0001-01                                True   
72085                 ANR-10-AALI-0001-02                               False   
72086                 ANR-10-AALI-0001-03                               False   
72087                 ANR-10-AALI-0001-04                               False   
72088                 ANR-10-AALI-0001-05                               False   

                         Projet.Partenaire.Nom_organisme  \
0      Centre interdisciplinaire de recherche en biol...   
1                           UNIVERSITE TOULOUSE CAPITOLE   
2      Interactions hotes-vecteurs-parasites-environn...   
3      CENTRE TECHNIQUE INDUSTRIEL DE LA PLASTURGIE E...   
4      Institut Pasteur - Unité de Virus et interfére...   
...                                                  ...   
72084  COMMISSARIAT A L'ENERGIE ATOMIQUE ET AUX ENERG...   
72085                                 AUTONOM'LAB (ALAB)   
72086                                         IDEES-3COM   
72087                     SPLITTED DESKTOP SYSTEMS (SDS)   
72088                                         IDEES-3COM   

      Projet.Partenaire.Categorie_organisme Projet.Partenaire.Code_RNSR  \
0                    Organisme de recherche                  201119724W   
1                                Université                  199511949P   
2                    Organisme de recherche                  201320629W   
3                              Divers privé                        None   
4                             Divers public                  201321615T   
...                                     ...                         ...   
72084                         Divers public                        None   
72085                            Université                        None   
72086    PME (petite et moyenne entreprise)                        None   
72087    PME (petite et moyenne entreprise)                        None   
72088    PME (petite et moyenne entreprise)                        None   

      Projet.Partenaire.Responsable_scientifique.Nom  \
0                                             BRUNET   
1                                             GRANDI   
2                                           BARREAUX   
3                                               ROCA   
4                                              SALEH   
...                                              ...   
72084                                         LOZADA   
72085                                           None   
72086                                           None   
72087                                           None   
72088                                        FLAMANT   

      Projet.Partenaire.Responsable_scientifique.Prenom  \
0                                              Isabelle   
1                  

In [ ]:
#compléter les données avec scanR
url_scanr='https://storage.gra.cloud.ovh.net/v1/AUTH_32c5d10cb0fe4519b957064a111717e3/scanR/projects.json'
requete_scanR = requests.get(url_scanr)
page_scanR= requete_scanR.json()
df_scanR=pd.DataFrame(page_scanR)
scanR=df_scanR.explode('participants').loc[:,['id','participants']]
scanR=scanR.rename(columns={'id':'id_anr'})
scanR['index']=[x for x in range(len(scanR))]
scanR=scanR.set_index('index')
scanR['id_structure_scanr']=scanR['participants'].apply(lambda x: x.get(str('structure')) if isinstance(x, dict) else None )
scanR['nom_struct']=scanR['participants'].apply(lambda x: get_scanR_structure(x))
del scanR['participants']
scanR_nettoye=scanR.drop_duplicates(subset='nom_struct')
scanR_nettoye[f"{sources[source]['nom_structure']}2"]=scanR_nettoye.loc[:,'nom_struct'].apply(lambda x: replace_all(str(x).lower()))
scanR_nettoye=scanR_nettoye[['id_structure_scanr',f"{sources[source]['nom_structure']}2"]]
scanR_nettoye=scanR_nettoye.drop_duplicates(subset=f"{sources[source]['nom_structure']}2")

C:\Users\haallat\AppData\Local\Temp\ipykernel_4372\2231553272.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  scanR_nettoye[f"{sources[source]['nom_structure']}2"]=scanR_nettoye.loc[:,'nom_struct'].apply(lambda x: replace_all(str(x).lower()))


In [15]:
df_partenaires_struct=pd.merge(df_partenaires_struct,scanR_nettoye, on=f"{sources[source]['nom_structure']}2", how='left')
df_partenaires_struct

Projet.Code_Decision_ANR Projet.Acronyme  \
0             ANR-24-SRSE-0016         MINerVA   
1             ANR-24-SRSE-0015            ADDI   
2             ANR-24-SRSE-0014       IMPACTING   
3             ANR-24-SRSE-0013         MERKATO   
4             ANR-24-SRSE-0012     inTOLERABLE   
...                        ...             ...   
72084         ANR-10-AALI-0001        ENTRANCE   
72085         ANR-10-AALI-0001        ENTRANCE   
72086         ANR-10-AALI-0001        ENTRANCE   
72087         ANR-10-AALI-0001        ENTRANCE   
72088         ANR-10-AALI-0001        ENTRANCE   

      Projet.Partenaire.Code_Decision_ANR  Projet.Partenaire.Est_coordinateur  \
0                     ANR-24-SRSE-0016-01                                True   
1                     ANR-24-SRSE-0015-01                                True   
2                     ANR-24-SRSE-0014-01                                True   
3                     ANR-24-SRSE-0013-01                                True   
4                     ANR-24-SRSE-0012-01                                True   
...                                   ...                                 ...   
72084                 ANR-10-AALI-0001-01                                True   
72085                 ANR-10-AALI-0001-02                               False   
72086                 ANR-10-AALI-0001-03                               False   
72087                 ANR-10-AALI-0001-04                               False   
72088                 ANR-10-AALI-0001-05                               False   

                         Projet.Partenaire.Nom_organisme  \
0      Centre interdisciplinaire de recherche en biol...   
1                           UNIVERSITE TOULOUSE CAPITOLE   
2      Interactions hotes-vecteurs-parasites-environn...   
3      CENTRE TECHNIQUE INDUSTRIEL DE LA PLASTURGIE E...   
4      Institut Pasteur - Unité de Virus et interfére...   
...                                                  ...   
72084  COMMISSARIAT A L'ENERGIE ATOMIQUE ET AUX ENERG...   
72085                                 AUTONOM'LAB (ALAB)   
72086                                         IDEES-3COM   
72087                     SPLITTED DESKTOP SYSTEMS (SDS)   
72088                                         IDEES-3COM   

      Projet.Partenaire.Categorie_organisme Projet.Partenaire.Code_RNSR  \
0                    Organisme de recherche                  201119724W   
1                                Université                  199511949P   
2                    Organisme de recherche                  201320629W   
3                              Divers privé                        None   
4                             Divers public                  201321615T   
...                                     ...                         ...   
72084                         Divers public                        None   
72085                            Université                        None   
72086    PME (petite et moyenne entreprise)                        None   
72087    PME (petite et moyenne entreprise)                        None   
72088    PME (petite et moyenne entreprise)                        None   

      Projet.Partenaire.Responsable_scientifique.Nom  \
0                                             BRUNET   
1                                             GRANDI   
2                                           BARREAUX   
3                                               ROCA   
4                                              SALEH   
...                                              ...   
72084                                         LOZADA   
72085                                           None   
72086                                           None   
72087                                           None   
72088                                        FLAMANT   

      Projet.Partenaire.Responsable_scientifique.Prenom  \
0                                              Isabelle   
1                  

In [16]:
#######fichier avec les identifiants structures rettrouvés à la main par Emmanuel ==> 'code'
scanr_structures=pd.read_excel('scanr_partenaires_non_identifies.xlsx')
scanr_structures[f"{sources[source]['nom_structure']}2"]=scanr_structures.loc[:,'Nom'].apply(lambda x: replace_all(str(x).lower().replace(" d e"," d'e").replace(" d a"," d'a").replace(" d i"," d'i").replace(" d o"," d'o").replace(" d u"," d'u").replace(" d y"," d'y").replace(" d h"," d'h").replace(" l e"," l'e").replace(" l a"," l'a").replace(" l i"," l'i").replace(" l o"," l'o").replace(" l u"," l'u").replace(" l y"," l'y").replace(" l h"," l'h")))
scanr_structures=scanr_structures[[f"{sources[source]['nom_structure']}2",'code']]
scanr_structures=scanr_structures.dropna().drop_duplicates(subset=f"{sources[source]['nom_structure']}2")
df_partenaires_complet=pd.merge(df_partenaires_struct,scanr_structures, on=f"{sources[source]['nom_structure']}2", how='left')
df_partenaires_complet

c:\Users\haallat\Anaconda3\lib\site-packages\openpyxl\worksheet\_reader.py:329: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


Projet.Code_Decision_ANR Projet.Acronyme  \
0             ANR-24-SRSE-0016         MINerVA   
1             ANR-24-SRSE-0015            ADDI   
2             ANR-24-SRSE-0014       IMPACTING   
3             ANR-24-SRSE-0013         MERKATO   
4             ANR-24-SRSE-0012     inTOLERABLE   
...                        ...             ...   
72084         ANR-10-AALI-0001        ENTRANCE   
72085         ANR-10-AALI-0001        ENTRANCE   
72086         ANR-10-AALI-0001        ENTRANCE   
72087         ANR-10-AALI-0001        ENTRANCE   
72088         ANR-10-AALI-0001        ENTRANCE   

      Projet.Partenaire.Code_Decision_ANR  Projet.Partenaire.Est_coordinateur  \
0                     ANR-24-SRSE-0016-01                                True   
1                     ANR-24-SRSE-0015-01                                True   
2                     ANR-24-SRSE-0014-01                                True   
3                     ANR-24-SRSE-0013-01                                True   
4                     ANR-24-SRSE-0012-01                                True   
...                                   ...                                 ...   
72084                 ANR-10-AALI-0001-01                                True   
72085                 ANR-10-AALI-0001-02                               False   
72086                 ANR-10-AALI-0001-03                               False   
72087                 ANR-10-AALI-0001-04                               False   
72088                 ANR-10-AALI-0001-05                               False   

                         Projet.Partenaire.Nom_organisme  \
0      Centre interdisciplinaire de recherche en biol...   
1                           UNIVERSITE TOULOUSE CAPITOLE   
2      Interactions hotes-vecteurs-parasites-environn...   
3      CENTRE TECHNIQUE INDUSTRIEL DE LA PLASTURGIE E...   
4      Institut Pasteur - Unité de Virus et interfére...   
...                                                  ...   
72084  COMMISSARIAT A L'ENERGIE ATOMIQUE ET AUX ENERG...   
72085                                 AUTONOM'LAB (ALAB)   
72086                                         IDEES-3COM   
72087                     SPLITTED DESKTOP SYSTEMS (SDS)   
72088                                         IDEES-3COM   

      Projet.Partenaire.Categorie_organisme Projet.Partenaire.Code_RNSR  \
0                    Organisme de recherche                  201119724W   
1                                Université                  199511949P   
2                    Organisme de recherche                  201320629W   
3                              Divers privé                        None   
4                             Divers public                  201321615T   
...                                     ...                         ...   
72084                         Divers public                        None   
72085                            Université                        None   
72086    PME (petite et moyenne entreprise)                        None   
72087    PME (petite et moyenne entreprise)                        None   
72088    PME (petite et moyenne entreprise)                        None   

      Projet.Partenaire.Responsable_scientifique.Nom  \
0                                             BRUNET   
1                                             GRANDI   
2                                           BARREAUX   
3                                               ROCA   
4                                              SALEH   
...                                              ...   
72084                                         LOZADA   
72085                                           None   
72086                                           None   
72087                                           None   
72088                                        FLAMANT   

      Projet.Partenaire.Responsable_scientifique.Prenom  \
0                                              Isabelle   
1                  

In [17]:
if 'finess' in list(df_partenaires.columns):
    finess_siret=pd.read_json("finess_siret-siege.json")
    df_partenaires_complet=pd.merge(df_partenaires_complet,finess_siret,how='left', on='finess')

In [18]:
df_partenaires_complet[sources[source]['identifiants_preferes_structure']]

Projet.Partenaire.Code_RNSR id_structure_matcher id_structure_scanr  \
0                      201119724W         [201119724W]         201119724W   
1                      199511949P                 None               None   
2                      201320629W         [201320629W]         201320629W   
3                            None                 None          353969348   
4                      201321615T         [201321615T]                NaN   
...                           ...                  ...                ...   
72084                        None                 None               None   
72085                        None                 None               None   
72086                        None                 None               None   
72087                        None                 None               None   
72088                        None                 None               None   

                 code  
0                 NaN  
1                 NaN  
2                 NaN  
3                 NaN  
4                 NaN  
...               ...  
72084  77568501900561  
72085  52202119500022  
72086  49197196600024  
72087  49264481000060  
72088  49197196600024  

[72089 rows x 4 columns]

In [19]:
df_partenaires_complet['id_structure']=df_partenaires_complet.apply(lambda row: identifiant_prefere(row,sources[source]['identifiants_preferes_structure']), axis=1)
df_partenaires_complet

Projet.Code_Decision_ANR Projet.Acronyme  \
0             ANR-24-SRSE-0016         MINerVA   
1             ANR-24-SRSE-0015            ADDI   
2             ANR-24-SRSE-0014       IMPACTING   
3             ANR-24-SRSE-0013         MERKATO   
4             ANR-24-SRSE-0012     inTOLERABLE   
...                        ...             ...   
72084         ANR-10-AALI-0001        ENTRANCE   
72085         ANR-10-AALI-0001        ENTRANCE   
72086         ANR-10-AALI-0001        ENTRANCE   
72087         ANR-10-AALI-0001        ENTRANCE   
72088         ANR-10-AALI-0001        ENTRANCE   

      Projet.Partenaire.Code_Decision_ANR  Projet.Partenaire.Est_coordinateur  \
0                     ANR-24-SRSE-0016-01                                True   
1                     ANR-24-SRSE-0015-01                                True   
2                     ANR-24-SRSE-0014-01                                True   
3                     ANR-24-SRSE-0013-01                                True   
4                     ANR-24-SRSE-0012-01                                True   
...                                   ...                                 ...   
72084                 ANR-10-AALI-0001-01                                True   
72085                 ANR-10-AALI-0001-02                               False   
72086                 ANR-10-AALI-0001-03                               False   
72087                 ANR-10-AALI-0001-04                               False   
72088                 ANR-10-AALI-0001-05                               False   

                         Projet.Partenaire.Nom_organisme  \
0      Centre interdisciplinaire de recherche en biol...   
1                           UNIVERSITE TOULOUSE CAPITOLE   
2      Interactions hotes-vecteurs-parasites-environn...   
3      CENTRE TECHNIQUE INDUSTRIEL DE LA PLASTURGIE E...   
4      Institut Pasteur - Unité de Virus et interfére...   
...                                                  ...   
72084  COMMISSARIAT A L'ENERGIE ATOMIQUE ET AUX ENERG...   
72085                                 AUTONOM'LAB (ALAB)   
72086                                         IDEES-3COM   
72087                     SPLITTED DESKTOP SYSTEMS (SDS)   
72088                                         IDEES-3COM   

      Projet.Partenaire.Categorie_organisme Projet.Partenaire.Code_RNSR  \
0                    Organisme de recherche                  201119724W   
1                                Université                  199511949P   
2                    Organisme de recherche                  201320629W   
3                              Divers privé                        None   
4                             Divers public                  201321615T   
...                                     ...                         ...   
72084                         Divers public                        None   
72085                            Université                        None   
72086    PME (petite et moyenne entreprise)                        None   
72087    PME (petite et moyenne entreprise)                        None   
72088    PME (petite et moyenne entreprise)                        None   

      Projet.Partenaire.Responsable_scientifique.Nom  \
0                                             BRUNET   
1                                             GRANDI   
2                                           BARREAUX   
3                                               ROCA   
4                                              SALEH   
...                                              ...   
72084                                         LOZADA   
72085                                           None   
72086                                           None   
72087                                           None   
72088                                        FLAMANT   

      Projet.Partenaire.Responsable_scientifique.Prenom  \
0                                              Isabelle   
1                  

In [20]:
#df_partenaires_complet[pd.isna(df_partenaires_complet.id_structure)]
df_partenaires_complet.loc[(pd.isna(df_partenaires_complet['id_structure']))|(str(df_partenaires_complet['id_structure'])=='None')|(str(df_partenaires_complet['id_structure'])=='nan')]

Projet.Code_Decision_ANR      Projet.Acronyme  \
21            ANR-24-RESO-0003             FAIRwDDI   
22            ANR-24-RESO-0003             FAIRwDDI   
23            ANR-24-RESO-0003             FAIRwDDI   
30            ANR-24-RESO-0001              OPEN IT   
34            ANR-24-QUA2-0007            ResourceQ   
...                        ...                  ...   
71533         ANR-10-BLAN-0602               eLIFE2   
71879         ANR-10-BIOT-0013          TSH testing   
71971         ANR-10-BIOE-0001               GAMECO   
72028         ANR-10-ALIA-0009  SafeFoodPack Design   
72030         ANR-10-ALIA-0009  SafeFoodPack Design   

      Projet.Partenaire.Code_Decision_ANR  Projet.Partenaire.Est_coordinateur  \
21                    ANR-24-RESO-0003-03                               False   
22                    ANR-24-RESO-0003-04                               False   
23                    ANR-24-RESO-0003-05                               False   
30                    ANR-24-RESO-0001-06                               False   
34                    ANR-24-QUA2-0007-01                                True   
...                                   ...                                 ...   
71533                 ANR-10-BLAN-0602-02                               False   
71879                 ANR-10-BIOT-0013-05                               False   
71971                 ANR-10-BIOE-0001-04                               False   
72028                 ANR-10-ALIA-0009-08                               False   
72030                 ANR-10-ALIA-0009-06                               False   

                         Projet.Partenaire.Nom_organisme  \
21                                          DDI Alliance   
22                                   Finish Data Archive   
23                    HUN-REN Centre for Social Sciences   
30                 Université de Modène et Reggio Emilia   
34     International Centre for Theory of Quantum Tec...   
...                                                  ...   
71533  CENTRE NATIONAL DE LA RECHERCHE SCIENTIFIQUE -...   
71879                CENTRE HOSPITALIER METROPOLE SAVOIE   
71971                                       EQTEC Iberia   
72028                                           Decernis   
72030  CENTRE D' APPUI ET DE STIMULATION DE L' INDUST...   

      Projet.Partenaire.Categorie_organisme Projet.Partenaire.Code_RNSR  \
21                 Fondation ou association                        None   
22                   Organisme de recherche                        None   
23                   Organisme de recherche                        None   
30                               Université                        None   
34                            Divers public                        None   
...                                     ...                         ...   
71533                Organisme de recherche                        None   
71879                       Hôpital / Santé                        None   
71971                            Université                        None   
72028                            Université                        None   
72030                            Université                        None   

      Projet.Partenaire.Responsable_scientifique.Nom  \
21                                              LYLE   
22                                           ALATERA   
23                                            GARDOS   
30                                         DE PRETIS   
34                                             SELBY   
...                                              ...   
71533                                          MARTY   
71879                                        GAUCHEZ   
71971                                        SANCHEZ   
72028                                     DESARNAUTS   
72030                                       THEBAULT   

      Projet.Partenaire.Responsable_scientifique.Prenom  \
21                

In [21]:
df_partenaires_complet.to_excel(f"./DATA/{source}/df_partenaires_id_structures.xlsx")
df_partenaires_complet.to_json(f"./DATA/{source}/df_partenaires_id_structures.json")

In [22]:
df_partenaires_complet=pd.read_json(f"./DATA/{source}/df_partenaires_id_structures.json")

In [23]:
########récupération des structures sans identifiants pour les donner à Emmanuel
identifiants_a_remplir=df_partenaires_complet.loc[(pd.isna(df_partenaires_complet['id_structure']))|(str(df_partenaires_complet['id_structure'])=='None')|(str(df_partenaires_complet['id_structure'])=='nan')]
identifiants_a_remplir
identifiants_a_remplir=identifiants_a_remplir.drop_duplicates(subset=f"{sources[source]['nom_structure']}2")
identifiants_a_remplir=identifiants_a_remplir.reset_index()
del identifiants_a_remplir['index']

In [24]:
###récupérer les structures avec les noms de chercheurs 
if source=='ADEME':
    identifiants_a_remplir['nom']=identifiants_a_remplir['Organisme du porteur'].apply(lambda x: str(x).split(' ')[0].capitalize())
    identifiants_a_remplir['prenom']=identifiants_a_remplir['Organisme du porteur'].apply(lambda x: extract_first_name(x))
    nom=[]
    prenom=[]
    id_structure=[]
    nom_structure=[]
    annees=[]
    annees_projet=[]
    idref=[]
    for i in range(len(identifiants_a_remplir)):
        r=get_data_from_elastic(url_cluster,f"{identifiants_a_remplir.iloc[i,:].prenom} {identifiants_a_remplir.iloc[i,:].nom}")
        if len(r['hits']['hits'])==1:
            if 'affiliations' in list(r['hits']['hits'][0]['_source'].keys()):
                for j in range(len(r['hits']['hits'][0]['_source']['affiliations'])):
                    annee_proj=[str(y) for y in range(int(identifiants_a_remplir.iloc[i,:]['Date de dÃ©but du projet'][:4]),int(identifiants_a_remplir.iloc[i,:]['Date de fin du projet'][:4])+1,1)]
                    if len([z for z in annee_proj if z in sorted(list(pd.Series([x['year'] for x in r['hits']['hits'][0]['_source']['affiliations'][j]['sources']]).drop_duplicates()))])>0:
                        nom.append(identifiants_a_remplir.iloc[i,:].nom)
                        prenom.append(identifiants_a_remplir.iloc[i,:].prenom)
                        idref.append(r['hits']['hits'][0]['_source']['id'])
                        annees_projet.append(annee_proj)
                        id_structure.append(r['hits']['hits'][0]['_source']['affiliations'][j]['structure']['id'])
                        nom_structure.append(r['hits']['hits'][0]['_source']['affiliations'][j]['structure']['label']['default'])
                        annees.append(sorted(list(pd.Series([x['year'] for x in r['hits']['hits'][0]['_source']['affiliations'][j]['sources']]).drop_duplicates())))
    df=pd.DataFrame(data={'nom':nom,'prenom':prenom,'idref':idref,'id_structure':id_structure,'nom_structure':nom_structure,'annees':annees,'annees_projet':annees_projet})
    df['structures_potentielles']=df.apply(lambda row: {"id" : row['id_structure'], "nom_structure": row['nom_structure']},axis=1)
    df=df.groupby(['nom','prenom','idref']).agg({'structures_potentielles':lambda x: list(x)}).reset_index()
    df2=pd.merge(identifiants_a_remplir,df, on=['nom','prenom'],how='left')
    df2.columns=['index', 'CatÃ©gorie', 'RÃ©fÃ©rence du projet', 'Acronyme du projet',
        'Titre du projet', "RÃ©fÃ©rence de l'appel Ã  projet",
        "Titre de l'appel Ã  projet", "Acronyme de l'appel Ã  projet",
        "AnnÃ©e de l'appel", 'Organisme du porteur', 'SIRET du porteur',
        'Identifiant ROR (Research Organization Registry) de lâorganisme ou RNSR',
        'Date de dÃ©but du projet', 'Date de fin du projet',
        'Organisme du porteur2', 'id_structure_matcher', 'id_structure_scanr',
        'code', 'id_structure', 'nom', 'prenom', 'idref','structures_potentielles']
    df2[['CatÃ©gorie', 'RÃ©fÃ©rence du projet', 'Acronyme du projet',
        'Titre du projet', "RÃ©fÃ©rence de l'appel Ã  projet",
        'Organisme du porteur',
        'Date de dÃ©but du projet', 'Date de fin du projet',
        'nom', 'prenom','idref','structures_potentielles']].to_excel(f"./structures_manquantes/partenaires_non_identifies_{source}.xlsx", index=False)

In [25]:
if source !='ADEME':   
    if sources[source]['ville'] in list(identifiants_a_remplir.columns) and sources[source]['pays'] in list(identifiants_a_remplir.columns) and sources[source]['adresse'] not in list(identifiants_a_remplir.columns):
        identifiants_a_remplir=identifiants_a_remplir[[sources[source]['nom_structure'],sources[source]['ville'],sources[source]['pays']]]
    elif sources[source]['ville'] in list(identifiants_a_remplir.columns) and sources[source]['pays'] in list(identifiants_a_remplir.columns) and sources[source]['adresse'] in list(identifiants_a_remplir.columns):
        identifiants_a_remplir=identifiants_a_remplir[[sources[source]['nom_structure'],sources[source]['adresse'],sources[source]['ville'],sources[source]['pays']]]
    elif sources[source]['region'] in list(identifiants_a_remplir.columns):
        identifiants_a_remplir=identifiants_a_remplir[[sources[source]['nom_structure'],sources[source]['region']]]
    elif sources[source]['ville'] in list(identifiants_a_remplir.columns) and sources[source]['pays'] not in list(identifiants_a_remplir.columns):
        identifiants_a_remplir=identifiants_a_remplir[[sources[source]['nom_structure'],sources[source]['ville']]]
    identifiants_a_remplir

In [26]:
if source != 'ADEME':
    identifiants_a_remplir.to_excel(f"./structures_manquantes/partenaires_non_identifies_{source}.xlsx", index=False)

# Matcher des chercheurs

In [27]:
df_partenaires=pd.read_json(f"./DATA/{source}/df_partenaires_id_structures.json")

In [ ]:
if len([x for x in ['nom', 'prenom'] if x in list(sources[source].keys())])==2:
    df_partenaires['id_personne']=df_partenaires.progress_apply(lambda row: get_person(row, cached_data_persons,sources[source]['nom'],sources[source]['prenom']), axis=1)
    write_cache(cached_data_persons,f"./DATA/{source}/caches/cached_data_persons.pkl")
    df_partenaires.to_excel(f"./DATA/{source}/df_partenaires_id_personne.xlsx")
    df_partenaires.to_json(f"./DATA/{source}/df_partenaires_id_personne.json")

  0%|          | 0/72089 [00:00<?, ?it/s]c:\Users\haallat\Anaconda3\lib\site-packages\bs4\builder\__init__.py:545: XMLParsedAsHTMLWarning: It looks like you're parsing an XML document using an HTML parser. If this really is an HTML document (maybe it's XHTML?), you can ignore or filter this warning. If it's XML, you should know that using an XML parser will be more reliable. To parse this document as XML, make sure you have the lxml package installed, and pass the keyword argument `features="xml"` into the BeautifulSoup constructor.
  warnings.warn(
  0%|          | 2/72089 [00:00<7:05:23,  2.82it/s]

no exact fullname match for BRUNET Isabelle vs ['isabelle brunet patru', 'brunet patru isabelle']
no exact fullname match for BRUNET Isabelle vs ['isabelle de gandt brunet', 'de gandt brunet isabelle']


  0%|          | 9/72089 [00:02<5:06:51,  3.91it/s]

no exact fullname match for HERVÉ Cécile vs ['anne cecile herve', 'herve anne cecile']
no exact fullname match for HERVÉ Cécile vs ['cecile herve bazin', 'herve bazin cecile']


  0%|          | 15/72089 [00:03<3:54:20,  5.13it/s]

...

no exact fullname match for None None vs ['laurent vecellio', 'vecellio laurent']


100%|█████████▉| 72088/72089 [4:31:41<00:00,  5.26it/s]

no exact fullname match for None None vs ['laurent vecellio', 'vecellio laurent']
no exact fullname match for None None vs ['laurent vecellio', 'vecellio laurent']


100%|██████████| 72089/72089 [4:31:41<00:00,  4.42it/s]

no exact fullname match for None None vs ['laurent vecellio', 'vecellio laurent']


In [29]:
if sources[source]['id_ORCID'] in list(df_partenaires.columns):
    df_partenaires=pd.read_json(f"./DATA/{source}/df_partenaires_id_personne.json")
    df_partenaires['idref_ORCID']=df_partenaires.progress_apply(lambda row: orcid_to_idref(row,cached_data_orcid,sources[source]['id_ORCID'],Authorization_ORCID), axis=1)
    write_cache(cached_data_orcid,f"./DATA/{source}/caches/cached_data_orcid.pkl")
    df_partenaires.to_excel(f"./DATA/{source}/df_partenaires_id_personne_ORCID.xlsx")
    df_partenaires.to_json(f"./DATA/{source}/df_partenaires_id_personne_ORCID.json")

100%|██████████| 72089/72089 [55:18<00:00, 21.73it/s]  


# ENVOI DES PROJETS SUR SCANR

In [30]:
if len(sources[source]['identifiants_preferes_personne'])==2:
    df_partenaires=pd.read_json(f"./DATA/{source}/df_partenaires_id_personne_ORCID.json")
elif len(sources[source]['identifiants_preferes_personne'])==1:
    df_partenaires=pd.read_json(f"./DATA/{source}/df_partenaires_id_personne.json")
else:
    df_partenaires=pd.read_json(f"./DATA/{source}/df_partenaires_id_structures.json")

In [65]:
df_partenaires.loc[df_partenaires.id_structure.apply(lambda x :isinstance(x,list)),'id_structure']=df_partenaires.loc[df_partenaires.id_structure.apply(lambda x :isinstance(x,list)),'id_structure'].apply(lambda y: y[0])

In [68]:
if len([x for x in ['nom', 'prenom'] if x in list(sources[source].keys())])==2:
    df_partenaires['id_person']=df_partenaires.apply(lambda row: identifiant_prefere(row,sources[source]['identifiants_preferes_personne']), axis=1)
    df_partenaires['persons']=df_partenaires.progress_apply(lambda row: persons(row,sources[source]['prenom'],sources[source]['nom']) ,axis=1)
else:
    df_partenaires['persons']=np.nan

100%|██████████| 72089/72089 [00:03<00:00, 20437.28it/s]


In [70]:
if source != 'SIRANO':
    df_partenaires=df_partenaires.groupby([sources[source]['code_projet']]).agg({'persons': lambda x: [ y for y in x.tolist() if pd.isna(y)==False]}, dropna=False).reset_index()
else:
    df_projets=df_partenaires.groupby([sources[source]['code_projet'], sources[source]['annee'], sources[source]['acronyme'],sources[source]['titre'],sources[source]['budget']], dropna=False).agg({'persons': lambda x: [ y for y in x.tolist() if pd.isna(y)==False]}, dropna=False)

In [71]:
# amener les projets depuis le site 
if source=='ANR':
    page_projets_10 = requests.get(sources[source]['url_projets']).json()
    colonnes_projets_10 = page_projets_10['columns']
    donnees_projets_10 = page_projets_10['data']
    df_projets=pd.DataFrame(data=donnees_projets_10,columns=colonnes_projets_10)
elif source=='IRESP':
    df_projets1=pd.read_csv(sources[source]['url_projets1'] ,sep=";", encoding='UTF-8')
    df_projets2=pd.read_csv(sources[source]['url_projets2'] ,sep=";", encoding='UTF-8')
    df_projets=pd.concat([df_projets1,df_projets2])
    df_projets.loc[pd.isna(df_projets['Titre_du_projet_FR']),'Titre_du_projet_FR']=df_projets.loc[pd.isna(df_projets['Titre_du_projet_FR']),'Titre_du_projet']
elif source!='SIRANO':
    df_projets=pd.read_csv(sources[source]['url_projets'] ,sep=";", encoding='ISO-8859-1')

df_projets=df_projets.reset_index()
del df_projets['index']

In [72]:
if source!='SIRANO':
    df_projets=pd.merge(df_projets,df_partenaires,on=sources[source]['code_projet'], how='left')
else :
    df_projets['id']=df_partenaires.apply(lambda row: f"{row[sources[source]['code_projet']]}-{row[sources[source]['annee']]}-{row[sources[source]['acronyme']]}" , axis=1)
    del df_projets['code_projet']
    sources[source]['code_projet']='id'

df_projets['type']=source
df_projets['name']=df_projets.progress_apply(lambda row: projects(row,sources[source]['titre_fr'],sources[source]['titre_en']) ,axis=1)
df_projets['description']=df_projets.progress_apply(lambda row: projects(row,sources[source]['resume_fr'],sources[source]['resume_en']) ,axis=1)
df_projets.loc[:,sources[source]['budget']]=df_projets.loc[:,sources[source]['budget']].apply(lambda x : float(str(x).replace('.0','').replace('.00','').replace(' ','').replace(',','.').replace('€','')))
df_projets=df_projets.rename(columns={sources[source]['annee']:'year',sources[source]['acronyme']:'acronym',
                                      sources[source]['budget']:'budget_financed',sources[source]['code_projet']:'id'})
df_projets=df_projets[['id','type','name','description','acronym','year','budget_financed','persons']]

100%|██████████| 22628/22628 [00:00<00:00, 24608.27it/s]


In [75]:
df_projets

id type  \
0      ANR-24-SRSE-0016  ANR   
1      ANR-24-SRSE-0015  ANR   
2      ANR-24-SRSE-0014  ANR   
3      ANR-24-SRSE-0013  ANR   
4      ANR-24-SRSE-0012  ANR   
...                 ...  ...   
22623  ANR-10-AALI-0005  ANR   
22624  ANR-10-AALI-0004  ANR   
22625  ANR-10-AALI-0003  ANR   
22626  ANR-10-AALI-0002  ANR   
22627  ANR-10-AALI-0001  ANR   

                                                    name  \
0      {'fr': 'Explorer l'interface neurovasculaire d...   
1      {'fr': 'Avancer l'innovation digitale démocrat...   
2      {'fr': 'Plate-forme multi-maladies vectorielle...   
3      {'fr': 'Innovations axées sur le marché pour l...   
4      {'fr': 'Rendre les moustiques intolérants aux ...   
...                                                  ...   
22623                                               None   
22624                                               None   
22625                                               None   
22626                                               None   
22627                                               None   

                                             description      acronym  year  \
0      {'fr': 'Le vaste réseau de nerfs périphériques...      MINerVA  2024   
1      {'fr': 'The Advancing Digital Democratic Innov...         ADDI  2024   
2      {'fr': 'Il est indispensable de déterminer la ...    IMPACTING  2024   
3      {'fr': 'Les emballages plastiques constituent ...      MERKATO  2024   
4      {'fr': 'L'incidence mondiale des maladies caus...  inTOLERABLE  2024   
...                                                  ...          ...   ...   
22623                                               None    STIMULATE  2010   
22624                                               None     NACODEAL  2010   
22625                                               None         LILY  2010   
22626                                               None         HOST  2010   
22627                                               None     ENTRANCE  2010   

       budget_financed                                            persons  
0             15457.50  [{'first_name': 'Isabelle', 'last_name': 'BRUN...  
1             16052.90  [{'id': 'idref224400711', 'first_name': 'Umber...  
2             16999.82  [{'id': 'idref253652642', 'first_name': 'Antoi...  
3            169974.00  [{'first_name': 'Bastien', 'last_name': 'ROCA'...  
4             15686.50  [{'id': 'idref176597514', 'first_name': 'Maria...  
...                ...                                                ...  
22623        196347.00  [{'role': 'scientific-officer###491282364'}, {...  
22624        196381.50       [{'role': 'scientific-officer###491282364'}]  
22625        379160.00  [{'role': 'scientific-officer###512338633'}, {...  
22626       1033012.93  [{'role': 'scientific-officer###22690001700014...  
22627       1120856.75  [{'id': 'idref131532650', 'first_name': 'José'...  

[22628 rows x 8 columns]

In [74]:
dict_row=df_projets.iloc[0,:].to_dict()
dict_row2={k:v for k,v in list(dict_row.items()) if ((str(v)!='nan')&(str(v)!='NaN')&(str(v)!='None')&(str(v)!='x')&(str(v)!='[]'))}
dict_row2

{'id': 'ANR-24-SRSE-0016',
 'type': 'ANR',
 'name': {'fr': "Explorer l'interface neurovasculaire des nerfs périphériques dans l'homéostasie, la pathologie et la réparation",
  'en': 'Unlocking the neurovascular interface of peripheral nerves in homeostasis, disease and repair'},
 'description': {'fr': 'Le vaste réseau de nerfs périphériques se développe simultanément et en contact étroit avec le système vasculaire. Cette relation spatiale et fonctionnelle persiste à l\'âge adulte, formant une interface neurovasculaire (NV) qui protège le tissu nerveux vulnérable par le biais d\'une barrière hémato-nerveuse (BNB), semblable à la barrière hémato-encéphalique (BBB). Malgré son rôle essentiel dans la santé du système nerveux périphérique (SNP), notre compréhension de l\'interface NV est limitée, ce qui a un impact sur la conception de thérapies pour les troubles du SNP liés à un dysfonctionnement vasculaire. Notre proposition interdisciplinaire vise à définir les caractéristiques moléculai

In [ ]:
#envoi
err=[]
for i,row in df_projets.iterrows():
    dict_row=row.to_dict()
    dict_row2={k:v for k,v in list(dict_row.items()) if ((str(v)!='nan')&(str(v)!='NaN')&(str(v)!='None')&(str(v)!='x')&(str(v)!='[]'))}
    try:
       r=requests.post('http://185.161.45.213/projects/projects', json = dict_row2, headers={"Authorization":Authorization})
       res= r.json()
       if res.get('status')=='ERR':
           err.append(res)
           if res.get('error').get('code')!=422:
               print(err)
               pp.pprint(err)
    except Exception as e:
        pp.pprint(e)

In [ ]:
pd.Series([x.get('issues').get('id') for x in err]).drop_duplicates().tolist() 

pour mettre à jour

In [76]:
nbr_page=int(requests.get('http://185.161.45.213/projects/projects?where={"type":"ANR"}&projection={"id":1}&max_results=500&page=1', headers={"Authorization":Authorization}).json()['hrefs']['last']['href'].split('page=')[1])

list_ids=[]
for i in range(1,nbr_page+1):
    print("page",i)
    page=requests.get('http://185.161.45.213/projects/projects?where={"type":"ANR"}&projection={"id":1}&max_results=500'+f"&page={i}", headers={"Authorization":Authorization}).json()
    for k in range(len(page['data'])):
        print("k",k)
        list_ids.append(page['data'][k]['id'])
    
projets_a_ajouter=[x for x in list(df_projets['id']) if x not in list_ids]

projets_a_retirer=[x for x in list_ids if x not in list(df_projets['id'])]

df_projets = df_projets[df_projets['id'].apply(lambda x: x in projets_a_ajouter)]

page 1
k 0
k 1
k 2
k 3
k 4
k 5
k 6
k 7
k 8
k 9
k 10
k 11
k 12
k 13
k 14
k 15
k 16
k 17
k 18
k 19
k 20
k 21
k 22
k 23
k 24
k 25
k 26
k 27
k 28
k 29
k 30
k 31
k 32
k 33
k 34
k 35
k 36
k 37
k 38
k 39
k 40
k 41
k 42
k 43
k 44
k 45
k 46
k 47
k 48
k 49
k 50
k 51
k 52
k 53
k 54
k 55
k 56
k 57
k 58
k 59
k 60
k 61
k 62
k 63
k 64
k 65
k 66
k 67
k 68
k 69
k 70
k 71
k 72
k 73
k 74
k 75
k 76
k 77
k 78
k 79
k 80
k 81
k 82
k 83
k 84
k 85
k 86
k 87
k 88
k 89
k 90
k 91
k 92
k 93
k 94
k 95
k 96
k 97
k 98
k 99
k 100
k 101
k 102
k 103
k 104
k 105
k 106
k 107
k 108
k 109
k 110
k 111
k 112
k 113
k 114
k 115
k 116
k 117
k 118
k 119
k 120
k 121
k 122
k 123
k 124
k 125
k 126
k 127
k 128
k 129
k 130
k 131
k 132
k 133
k 134
k 135
k 136
k 137
k 138
k 139
k 140
k 141
k 142
k 143
k 144
k 145
k 146
k 147
k 148
k 149
k 150
k 151
k 152
k 153
k 154
k 155
k 156
k 157
k 158
k 159
k 160
k 161
k 162
k 163
k 164
k 165
k 166
k 167
k 168
k 169
k 170
k 171
k 172
k 173
k 174
k 175
k 176
k 177
k 178
k 179
k 180
k 181
k 182
k 183

In [80]:
dict_row=df_projets.iloc[0,:].to_dict()
dict_row2={k:v for k,v in list(dict_row.items()) if ((str(v)!='nan')&(str(v)!='NaN')&(str(v)!='None')&(str(v)!='x')&(str(v)!='[]'))}
dict_row2

{'id': 'ANR-24-SRSE-0016',
 'type': 'ANR',
 'name': {'fr': "Explorer l'interface neurovasculaire des nerfs périphériques dans l'homéostasie, la pathologie et la réparation",
  'en': 'Unlocking the neurovascular interface of peripheral nerves in homeostasis, disease and repair'},
 'description': {'fr': 'Le vaste réseau de nerfs périphériques se développe simultanément et en contact étroit avec le système vasculaire. Cette relation spatiale et fonctionnelle persiste à l\'âge adulte, formant une interface neurovasculaire (NV) qui protège le tissu nerveux vulnérable par le biais d\'une barrière hémato-nerveuse (BNB), semblable à la barrière hémato-encéphalique (BBB). Malgré son rôle essentiel dans la santé du système nerveux périphérique (SNP), notre compréhension de l\'interface NV est limitée, ce qui a un impact sur la conception de thérapies pour les troubles du SNP liés à un dysfonctionnement vasculaire. Notre proposition interdisciplinaire vise à définir les caractéristiques moléculai

In [81]:
err=[]
for i,row in df_projets.iterrows():
    dict_row=row.to_dict()
    dict_row2={k:v for k,v in list(dict_row.items()) if ((str(v)!='nan')&(str(v)!='NaN')&(str(v)!='None')&(str(v)!='x')&(str(v)!='[]'))}
    try:
       r=requests.post('http://185.161.45.213/projects/projects', json = dict_row2, headers={"Authorization":Authorization})
       res= r.json()
       if res.get('status')=='ERR':
           err.append(res)
           if res.get('error').get('code')!=422:
               print(err)
               pp.pprint(err)
    except Exception as e:
        pp.pprint(e)

In [79]:
len(projets_a_ajouter)

872

Modifications

In [148]:
nbr_page=int(requests.get('http://185.161.45.213/projects/projects?where={"type":"ANR"}&projection={"id":1,"year":1}&max_results=500'+f"&page={1}", headers={"Authorization":Authorization}).json()['hrefs']['last']['href'].split('page=')[1])
nbr_page

46

In [154]:
list_ids=[]
for i in range(1,nbr_page+1):
    print("page",i)
    page=requests.get('http://185.161.45.213/projects/projects?where={%22type%22:%22ANR%22}&projection={%22id%22:1,%22year%22:1}&max_results=500'+f"&page={i}", headers={"Authorization":Authorization}).json()
    for k in range(len(page['data'])):
        list_ids.append(page['data'][k]['year'])

page 1
page 2
page 3
page 4
page 5
page 6
page 7
page 8
page 9
page 10
page 11
page 12
page 13
page 14
page 15
page 16
page 17
page 18
page 19
page 20
page 21
page 22
page 23
page 24
page 25
page 26
page 27
page 28
page 29
page 30
page 31
page 32
page 33
page 34
page 35
page 36
page 37
page 38
page 39
page 40
page 41
page 42
page 43
page 44
page 45
page 46


In [155]:
max(list_ids)

2024

In [ ]:
df_projets = df_projets[df_projets['id'].apply(lambda x: x in list_ids)]

In [ ]:
"""
en principe, il faut que je je mette à jour tous les projets 
qui ne sont pas clos avec les titres résumés et persons, mais 
peut etre qu'on peut mettre à jour automatiquement les projets
des 3 dernières années ? 

"""

err=[]
for id in df_projets.iterrows() :
    url = f"http://185.161.45.213/projects/projects/{id}"
    project=requests.get(url, headers={'Authorization': Authorization}).json()
    head = {"Authorization": Authorization, "If-Match": project['etag'], "Content-Type": "application/json"}

    r = requests.patch(url, json = {"year": 2023}, headers=head)
    res= r.json()
    if res.get('status')=='ERR':
        err.append(res)
        if res.get('error').get('code')!=422:
            print(err)
            pp.pprint(err)


# ENVOI DES PARTENAIRES SUR SCANR

In [111]:
df_partenaires=pd.read_json(f"./DATA/{source}/df_partenaires_id_structures.json")

In [112]:
df_partenaires.columns

Index(['Projet.Code_Decision_ANR', 'Projet.Acronyme',
       'Projet.Partenaire.Code_Decision_ANR',
       'Projet.Partenaire.Est_coordinateur', 'Projet.Partenaire.Nom_organisme',
       'Projet.Partenaire.Categorie_organisme', 'Projet.Partenaire.Code_RNSR',
       'Projet.Partenaire.Responsable_scientifique.Nom',
       'Projet.Partenaire.Responsable_scientifique.Prenom',
       'Projet.Partenaire.Responsable_scientifique.ORCID',
       'Projet.Partenaire.Adresse.Ville', 'Projet.Partenaire.Adresse.Region',
       'Projet.Partenaire.Adresse.Pays', 'Projet.Partenaire.Aide_allouee.ANR',
       'Projet.Partenaire.Financement.Source',
       'Projet.Partenaire.Nom_organisme2', 'id_structure_matcher',
       'id_structure_scanr', 'code', 'id_structure'],
      dtype='object')

In [113]:
### ATTENTION, vérifier que les projets sirano sont dans des structures françaises
if source=='IRESP':
    df_partenaires[sources[source]['pays']]=df_partenaires.loc[:,sources[source]['ville']].apply(lambda x: x.split('(')[1].replace(')','') if x.find('(')>=0 else 'France')
    df_partenaires.loc[:,sources[source]['ville']]=df_partenaires.loc[:,sources[source]['ville']].apply(lambda x: x.split('(')[0] if x.find('(')>=0 else x)
  
df_partenaires['address']=df_partenaires.apply(lambda row: address(row,sources[source]['pays'],sources[source]['ville'],source), axis=1)
df_partenaires.loc[:,'id_structure']=df_partenaires.loc[:,'id_structure'].apply(lambda x: x[0] if isinstance(x,list) else x )

In [114]:
if source in ['ANSES','SIRANO']:
    df_partenaires['id']=df_partenaires.apply(lambda row: f"{row[sources[source]['code_projet']]}-{row[{sources[source]['nom_structure']}+'2']}-{row[sources[source]['nom']]}-{row[sources[source]['prenom']]}" , axis=1)
if source =='REG_IDF':
    df_partenaires['id']=df_partenaires.apply(lambda row: f"{row[sources[source]['code_projet']]}-{row[str(sources[source]['nom_structure'])+'2']}-{row['entite_role']}" , axis=1)
df_partenaires['address']=df_partenaires.apply(lambda row: address(row,sources[source]['pays'],sources[source]['ville'],source), axis=1)
df_partenaires=df_partenaires.rename(columns={sources[source]['nom_structure']: 'name', sources[source]['code_projet']: 'project_id', 'id_structure':'participant_id','Projet.Partenaire.Code_Decision_ANR':'id'})
df_partenaires=df_partenaires[['name','id','project_id','participant_id','address']]
df_partenaires['project_type']=source
df_partenaires['participant_id']=df_partenaires.loc[:,'participant_id'].apply(lambda x: str(x[0]).replace('.0','') if isinstance(x,list) else str(x).split(';')[0].replace('.0',''))
df_partenaires=df_partenaires[['id','project_id', 'project_type', 'participant_id', 'name','address']]
df_partenaires['name'] = df_partenaires['name'].astype(str)
df_partenaires

id        project_id project_type  participant_id  \
0      ANR-24-SRSE-0016-01  ANR-24-SRSE-0016          ANR      201119724W   
1      ANR-24-SRSE-0015-01  ANR-24-SRSE-0015          ANR      199511949P   
2      ANR-24-SRSE-0014-01  ANR-24-SRSE-0014          ANR      201320629W   
3      ANR-24-SRSE-0013-01  ANR-24-SRSE-0013          ANR       353969348   
4      ANR-24-SRSE-0012-01  ANR-24-SRSE-0012          ANR      201321615T   
...                    ...               ...          ...             ...   
72084  ANR-10-AALI-0001-01  ANR-10-AALI-0001          ANR  77568501900561   
72085  ANR-10-AALI-0001-02  ANR-10-AALI-0001          ANR  52202119500022   
72086  ANR-10-AALI-0001-03  ANR-10-AALI-0001          ANR  49197196600024   
72087  ANR-10-AALI-0001-04  ANR-10-AALI-0001          ANR  49264481000060   
72088  ANR-10-AALI-0001-05  ANR-10-AALI-0001          ANR  49197196600024   

                                                    name  \
0      Centre interdisciplinaire de recherche en biol...   
1                           UNIVERSITE TOULOUSE CAPITOLE   
2      Interactions hotes-vecteurs-parasites-environn...   
3      CENTRE TECHNIQUE INDUSTRIEL DE LA PLASTURGIE E...   
4      Institut Pasteur - Unité de Virus et interfére...   
...                                                  ...   
72084  COMMISSARIAT A L'ENERGIE ATOMIQUE ET AUX ENERG...   
72085                                 AUTONOM'LAB (ALAB)   
72086                                         IDEES-3COM   
72087                     SPLITTED DESKTOP SYSTEMS (SDS)   
72088                                         IDEES-3COM   

                                            address  
0            {'city': 'PARIS', 'country': 'France'}  
1         {'city': 'Toulouse', 'country': 'France'}  
2      {'city': 'Montpellier', 'country': 'France'}  
3        {'city': 'Bellignat', 'country': 'France'}  
4            {'city': 'Paris', 'country': 'France'}  
...                                             ...  
72084                         {'country': 'France'}  
72085                         {'country': 'France'}  
72086                         {'country': 'France'}  
72087                         {'country': 'France'}  
72088      {'city': 'Roubaix', 'country': 'France'}  

[72089 rows x 6 columns]

In [115]:
df_partenaires[df_partenaires.duplicated(subset=['id'])]

Empty DataFrame
Columns: [id, project_id, project_type, participant_id, name, address]
Index: []

In [116]:
dict_row=df_partenaires.iloc[1,:].to_dict()
dict_row2={k:v for k,v in list(dict_row.items()) if ((str(v)!='nan')&(str(v)!='NaN')&(str(v)!='None')&(str(v)!='x'))}
dict_row2

{'id': 'ANR-24-SRSE-0015-01',
 'project_id': 'ANR-24-SRSE-0015',
 'project_type': 'ANR',
 'participant_id': '199511949P',
 'name': 'UNIVERSITE TOULOUSE CAPITOLE',
 'address': {'city': 'Toulouse', 'country': 'France'}}

In [105]:
len(df_partenaires)

72089

In [ ]:
err=[]
for i,row in df_partenaires.iterrows():
    dict_row=row.to_dict()
    dict_row2={k:v for k,v in list(dict_row.items()) if ((str(v)!='nan')&(str(v)!='NaN')&(str(v)!='None')&(str(v)!='x'))}
    try:
       r=requests.post('http://185.161.45.213/projects/participations', json = dict_row2, headers={"Authorization":Authorization})
       res= r.json()
       if res.get('status')=='ERR':
           print(i)
           err.append(res)
           if res.get('error').get('code')!=422:
               print(err)
               pp.pprint(err)
    except Exception as e:
        pp.pprint(e)

Mise à jour

In [106]:
nbr_page=int(requests.get('http://185.161.45.213/projects/participations?where={"project_type":"ANR"}&projection={"id":1}&max_results=500&page=1', headers={"Authorization":Authorization}).json()['hrefs']['last']['href'].split('page=')[1])

list_ids=[]
for i in range(1,nbr_page+1):
    print("page",i)
    page=requests.get('http://185.161.45.213/projects/participations?where={"project_type":"ANR"}&projection={"id":1}&max_results=500'+f"&page={i}", headers={"Authorization":Authorization}).json()
    for k in range(len(page['data'])):
        print("k",k)
        list_ids.append(page['data'][k]['id'])
    
projets_a_ajouter=[x for x in list(df_partenaires['id'].drop_duplicates()) if x not in list(pd.Series(list_ids).drop_duplicates())]

projets_a_retirer=[x for x in list_ids if x not in list(df_partenaires['id'])]

df_partenaires = df_partenaires[df_partenaires['id'].apply(lambda x: x in projets_a_ajouter)]


page 1
k 0
k 1
k 2
k 3
k 4
k 5
k 6
k 7
k 8
k 9
k 10
k 11
k 12
k 13
k 14
k 15
k 16
k 17
k 18
k 19
k 20
k 21
k 22
k 23
k 24
k 25
k 26
k 27
k 28
k 29
k 30
k 31
k 32
k 33
k 34
k 35
k 36
k 37
k 38
k 39
k 40
k 41
k 42
k 43
k 44
k 45
k 46
k 47
k 48
k 49
k 50
k 51
k 52
k 53
k 54
k 55
k 56
k 57
k 58
k 59
k 60
k 61
k 62
k 63
k 64
k 65
k 66
k 67
k 68
k 69
k 70
k 71
k 72
k 73
k 74
k 75
k 76
k 77
k 78
k 79
k 80
k 81
k 82
k 83
k 84
k 85
k 86
k 87
k 88
k 89
k 90
k 91
k 92
k 93
k 94
k 95
k 96
k 97
k 98
k 99
k 100
k 101
k 102
k 103
k 104
k 105
k 106
k 107
k 108
k 109
k 110
k 111
k 112
k 113
k 114
k 115
k 116
k 117
k 118
k 119
k 120
k 121
k 122
k 123
k 124
k 125
k 126
k 127
k 128
k 129
k 130
k 131
k 132
k 133
k 134
k 135
k 136
k 137
k 138
k 139
k 140
k 141
k 142
k 143
k 144
k 145
k 146
k 147
k 148
k 149
k 150
k 151
k 152
k 153
k 154
k 155
k 156
k 157
k 158
k 159
k 160
k 161
k 162
k 163
k 164
k 165
k 166
k 167
k 168
k 169
k 170
k 171
k 172
k 173
k 174
k 175
k 176
k 177
k 178
k 179
k 180
k 181
k 182
k 183

In [107]:
len(projets_a_ajouter)

9

In [108]:
err=[]
for i,row in df_partenaires.iterrows():
    dict_row=row.to_dict()
    dict_row2={k:v for k,v in list(dict_row.items()) if ((str(v)!='nan')&(str(v)!='NaN')&(str(v)!='None')&(str(v)!='x'))}
    try:
       r=requests.post('http://185.161.45.213/projects/participations', json = dict_row2, headers={"Authorization":Authorization})
       res= r.json()
       if res.get('status')=='ERR':
           print(i)
           err.append(res)
           if res.get('error').get('code')!=422:
               print(err)
               pp.pprint(err)
    except Exception as e:
        pp.pprint(e)

Modifications

In [141]:
nbr_page=int(requests.get('http://185.161.45.213/projects/participations?where={"project_type":"ANR","participant_id":{"$exists":false}}&projection={"id":1}&max_results=500'+f"&page={1}", headers={"Authorization":Authorization}).json()['hrefs']['last']['href'].split('page=')[1])

list_ids=[]
for i in range(1,nbr_page+1):
    print("page",i)
    page=requests.get('http://185.161.45.213/projects/participations?where={"project_type":"ANR","participant_id":{"$exists":false}}&projection={"id":1}&max_results=500'+f"&page={i}", headers={"Authorization":Authorization}).json()
    for k in range(len(page['data'])):
        print("k",k)
        list_ids.append(page['data'][k]['id'])

df_partenaires = df_partenaires[df_partenaires['id'].apply(lambda x: x in list_ids)]

page 1
k 0
k 1
k 2
k 3
k 4
k 5
k 6
k 7
k 8
k 9
k 10
k 11
k 12
k 13
k 14
k 15
k 16
k 17
k 18
k 19
k 20
k 21
k 22
k 23
k 24
k 25
k 26
k 27
k 28
k 29
k 30
k 31
k 32
k 33
k 34
k 35
k 36
k 37
k 38
k 39
k 40
k 41
k 42
k 43
k 44
k 45
k 46
k 47
k 48
k 49
k 50
k 51
k 52
k 53
k 54
k 55
k 56
k 57
k 58
k 59
k 60
k 61
k 62
k 63
k 64
k 65
k 66
k 67
k 68
k 69
k 70
k 71
k 72
k 73
k 74
k 75
k 76
k 77
k 78
k 79
k 80
k 81
k 82
k 83
k 84
k 85
k 86
k 87
k 88
k 89
k 90
k 91
k 92
k 93
k 94
k 95
k 96
k 97
k 98
k 99
k 100
k 101
k 102
k 103
k 104
k 105
k 106
k 107
k 108
k 109
k 110
k 111
k 112
k 113
k 114
k 115
k 116
k 117
k 118
k 119
k 120
k 121
k 122
k 123
k 124
k 125
k 126
k 127
k 128
k 129
k 130
k 131
k 132
k 133
k 134
k 135
k 136
k 137
k 138
k 139
k 140
k 141
k 142
k 143
k 144
k 145
k 146
k 147
k 148
k 149
k 150
k 151
k 152
k 153
k 154
k 155
k 156
k 157
k 158
k 159
k 160
k 161
k 162
k 163
k 164
k 165
k 166
k 167
k 168
k 169
k 170
k 171
k 172
k 173
k 174
k 175
k 176
k 177
k 178
k 179
k 180
k 181
k 182
k 183

In [143]:
len(list_ids)

3575

In [127]:
df_partenaires=df_partenaires[(df_partenaires.participant_id!='x') & (df_partenaires.participant_id!='None')]

In [128]:
df_partenaires

id        project_id project_type  participant_id  \
3467   ANR-23-SSRP-0017-08  ANR-23-SSRP-0017          ANR  48187239800021   
3469   ANR-23-SSRP-0017-06  ANR-23-SSRP-0017          ANR  42108823800066   
3470   ANR-23-SSRP-0017-04  ANR-23-SSRP-0017          ANR  49457785100020   
3485   ANR-23-SSRP-0014-05  ANR-23-SSRP-0014          ANR  79068864200020   
3487   ANR-23-SSRP-0014-06  ANR-23-SSRP-0014          ANR  40271012300025   
...                    ...               ...          ...             ...   
72052  ANR-10-ALIA-0003-04  ANR-10-ALIA-0003          ANR  38136114600032   
72070  ANR-10-AALI-0006-04  ANR-10-AALI-0006          ANR  38531156800039   
72079  ANR-10-AALI-0003-02  ANR-10-AALI-0003          ANR  13002249400111   
72082  ANR-10-AALI-0002-01  ANR-10-AALI-0002          ANR  77985929700383   
72087  ANR-10-AALI-0001-04  ANR-10-AALI-0001          ANR  49264481000060   

                                                    name  \
3467   FAB'LIM, Le Labo des Territoires Alimentaires ...   
3469                         Relais d'sciences - Le Dôme   
3470                                              TRACES   
3485                                     Amis du Maitron   
3487               Amis de la Fondation de la Résistance   
...                                                  ...   
72052  SOCIETE D' APPLICATIONS DE RECHERCHES ET DE CO...   
72070                                              ASICA   
72079  CHAMBRE DE COMMERCE ET D' INDUSTRIE DE LA CREU...   
72082        OFFICE PUBLIC DE L HABITAT DU RHÔNE (OPAC )   
72087                     SPLITTED DESKTOP SYSTEMS (SDS)   

                                         address  
3467   {'city': 'Pomerols', 'country': 'France'}  
3469       {'city': 'Caen', 'country': 'France'}  
3470      {'city': 'PARIS', 'country': 'France'}  
3485                                        None  
3487                                        None  
...                                          ...  
72052   {'city': 'Floirac', 'country': 'France'}  
72070                      {'country': 'France'}  
72079                      {'country': 'France'}  
72082                      {'country': 'France'}  
72087                      {'country': 'France'}  

[4169 rows x 6 columns]

In [140]:
err=[]
for i,row in df_partenaires.iterrows() :
    print(i)
    id=row['id']
    url = f"http://185.161.45.213/projects/participations/{id}"
    project=requests.get(url, headers={'Authorization': Authorization}).json()
    head = {"Authorization": Authorization, "If-Match": project['etag'], "Content-Type": "application/json"}

    r = requests.patch(url, json = {"participant_id": row['participant_id']}, headers=head)
    res= r.json()
    if res.get('status')=='ERR':
        err.append(res)
        if res.get('error').get('code')!=422:
            print(err)
            pp.pprint(err)

3467
3469
3470
3485
3487
3494
3496
3501
3503
3521
3531
3539
3542
3548
3551
3559
3564
3567
3569
3571
3574
3575
3579
3583
3587
3591
3594
3597
3612
3665
3677
3693
3714
3718
3729
3738
3752
3761
3770
3777
3786
3799
3822
3890
3905
3915
3919
3922
3939
3940
3941
3943
3944
3945
3947
3971
3983
3994
3999
4006
4007
4010
4012
4015
4016
4020
4023
4024
4030
4041
4044
4050
4053
4055
4074
4076
4079
4081
4085
4090
4099
4100
4101
4102
4112
4113
4120
4121
4140
4142
4145
4155
4158
4160
4176
4178
4189
4224
4227
4228
4258
4259
4262
4272
4275
4277
4287
4324
4325
4328
4329
4332
4352
4353
4358
4368
4372
4377
4379
4380
4382
4383
4389
4390
4396
4397
4400
4406
4414
4419
4425
4427
4433
4450
4453
4471
4476
4480
4491
4511
4515
4516
4518
4545
4548
4549
4551
4563
4571
4574
4580
4585
4596
4636
4638
4640
4641
4651
4657
4658
4659
4662
4663
4703
4704
4734
4744
4756
4768
4778
4814
4827
4847
4868
4870
4871
4878
4926
4935
4949
4952
4957
4964
4966
4970
4975
4976
4979
5022
5041
5044
5048
5056
5069
5070
5082
5083
5085
5091
5104


In [ ]:
pd.Series([x.get('issues').get('id')[25:] for x in err]).drop_duplicates().tolist()